In [22]:
%env NX_CURGAPH_AUTOCONFIG=True
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
import numpy as np
import osmnx as ox
from math import sqrt
location = (39.21732, -76.52815)

env: NX_CURGAPH_AUTOCONFIG=True


# 数据处理

In [20]:

G_ox = ox.graph_from_point(location, dist=10000, network_type='drive')  # 从OpenStreetMap下载数据
G_nx = nx.DiGraph(G_ox)  # 标准NetworkX有向图
# 从OpenStreetMap下载的数据中提取节点和边的信息
nodes, edges = ox.graph_to_gdfs(G_ox)
# 存储节点和边的信息
nodes.to_csv('data/extra/nodes_drive.csv')
edges.to_csv('data/extra/edges_drive.csv')

# 进行合并

In [26]:
edges_drive = pd.read_csv('data/edges_drive.csv')
nodes_drive = pd.read_csv('data/nodes_drive.csv')
edges_drive_extra = pd.read_csv('data/extra/edges_drive.csv')
nodes_drive_extra = pd.read_csv('data/extra/nodes_drive.csv')
# 合并
edges_drive = pd.concat([edges_drive, edges_drive_extra])
nodes_drive = pd.concat([nodes_drive, nodes_drive_extra])
# 去重
edges_drive = edges_drive.drop_duplicates()
nodes_drive = nodes_drive.drop_duplicates()
# 保存
edges_drive.to_csv('data/edges_drive_merge.csv', index=False)
nodes_drive.to_csv('data/nodes_drive_merge.csv', index=False)

C:\Users\wzh20\AppData\Local\Temp\ipykernel_72296\2228325504.py:1: DtypeWarning: Columns (18) have mixed types. Specify dtype option on import or set low_memory=False.
  edges_drive = pd.read_csv('data/edges_drive.csv')


In [27]:
edges_all = pd.read_csv('data/edges_drive_merge.csv')


C:\Users\wzh20\AppData\Local\Temp\ipykernel_72296\2775732312.py:1: DtypeWarning: Columns (18) have mixed types. Specify dtype option on import or set low_memory=False.
  edges_all = pd.read_csv('data/edges_drive_merge.csv')


In [28]:
edges_all["lanes"] = pd.to_numeric(edges_all["lanes"], errors="coerce")
edges_all["maxspeed"] = edges_all["maxspeed"].apply(
    lambda x: x.replace("mph", "").strip() if isinstance(x, str) else x
)
# 如果 'maxspeed' 列包含像 ['45 ', '60 '] 这样的列表，取出第一个值
edges_all["maxspeed"] = edges_all["maxspeed"].apply(
    lambda x: eval(x)[0] if isinstance(x, str) and x.startswith("[") else x
)
edges_all["maxspeed"] = pd.to_numeric(edges_all["maxspeed"], errors="coerce")
edges_all["lanes"].fillna(edges_all["lanes"].median(), inplace=True)
edges_all["maxspeed"].fillna(edges_all["maxspeed"].median(), inplace=True)


C:\Users\wzh20\AppData\Local\Temp\ipykernel_72296\3800771457.py:10: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  edges_all["lanes"].fillna(edges_all["lanes"].median(), inplace=True)
C:\Users\wzh20\AppData\Local\Temp\ipykernel_72296\3800771457.py:11: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behav

In [29]:
nodes_all = pd.read_csv('data/nodes_drive_merge.csv')
pos=dict()
for _,row in nodes_all.iterrows():
    pos[row['osmid']]=(row['x'],row['y'])

# 绘图

In [30]:
alpha, beta, gamma = 0.5, 0.4, 0.5


def calculate_weight(row):
    length_weight = row["length"] / max_length
    aadt_weight = 0
    #aadt_weight = row["AADT 2022"] / max_aadt
    lanes_weight = row["lanes"] / max_lanes
    return alpha * length_weight + beta * aadt_weight + gamma * lanes_weight

max_length = edges_all["length"].max()
#max_aadt = edges_all["AADT 2022"].max()
max_lanes = edges_all["lanes"].max()
for _, row in edges_all.iterrows():
    edges_all.loc[_, "weight"] = calculate_weight(row)

In [ ]:
G = nx.DiGraph()
cnt = 0


rng = 0.3


def getdis(x, y):
    return sqrt((x[0] - y[1]) ** 2 + (x[1] - y[0]) ** 2)


for _, row in edges_all.iterrows():
    if row["u"] == row["v"]:
        continue
    if getdis(pos[row["u"]], location) > rng or getdis(pos[row["v"]], location) > rng:
        continue
    cnt += 1
    # if cnt>10000:
    # break
    G.add_edge(
        row["u"],
        row["v"],
        weight=row["weight"],
        length=row["length"],
        lanes=row["lanes"],
        maxspeed=row["maxspeed"],
    )
print(cnt)

28742


In [32]:
from tqdm import tqdm 

plt.figure(figsize=(100,100))
print("Drawing nodes")
#nx.draw_networkx_nodes(G,pos,node_size=1,node_color='blue',alpha=0.3)
print("Drawing edges")
nx.draw_networkx_edges(G,pos,edge_color='gray',width=3,style='dashed')
print("Drawing high weight edges")
#high_weight_edges = [(u, v) for u, v, d in G.edges(data=True) if d['weight'] > 0.15]
#nx.draw_networkx_edges(G,pos,edgelist=high_weight_edges,edge_color='red',width=5,style='solid') 

plt.show()


Drawing nodes
Drawing edges
Drawing high weight edges


In [ ]:
plt.savefig("imgs/road_network.svg")  

# 流量分配

## 读入数据

In [ ]:
traffic_data = pd.read_csv('data/MDOT_SHA_Annual_Average_Daily_Traffic_Baltimore.csv')
edges_all = pd.read_csv('data/edges_all.csv')
nodes_all = pd.read_csv('data/nodes_all.csv')
edges,traffic,nodes = [],[],[]
for _,row in traffic_data.iterrows():
    traffic.append(row)
for _,row in edges_all.iterrows():
    edges.append(row)
for _,row in nodes_all.iterrows():
    nodes.append(row)

# 处理数据

In [ ]:
for i in tqdm(range(len(edges))):
    edges[i]['u'] = int(edges[i]['u'])
    edges[i]['v'] = int(edges[i]['v'])
    edges[i]['lanes'] = int(edges[i]['lanes'])
    edges[i]['length'] = float(edges[i]['length'])
    edges[i]['weight'] = float(edges[i]['weight'])